# <span style="color:purple"> Pandas Notebook 2, ATM350 Spring 2024 </span>

## Motivating Science Questions:
1. What was the daily temperature and precipitation at Albany last year?
2. What were the the days with the most precipitation?

## Motivating Technical Question:
1. How can we use Pandas to do some basic statistical analyses of our data?

### We'll start by repeating some of the same steps we did in the first Pandas notebook.

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
sns.set()

In [ ]:
file = '/spare11/atm350/common/data/climo_alb_2023.csv'

Display the first five lines of this file using Python's built-in `readline` function

In [ ]:
fileObj = open(file)
nLines = 5
for n in range(nLines):
    line = fileObj.readline()
    print(line)

In [ ]:
df = pd.read_csv(file, dtype='string')

nRows = df.shape[0]
print ("Number of rows = %d" % nRows )
nCols = df.shape[1]
print ("Number of columns = %d" % nCols)

date = df['DATE']
date = pd.to_datetime(date,format="%Y-%m-%d")

maxT = df['MAX'].astype("float32")
minT = df['MIN'].astype("float32")

### Let's generate the final timeseries we made in our first Pandas notebook, with all the "bells and whistles" included.

In [ ]:
from matplotlib.dates import DateFormatter, AutoDateLocator,HourLocator,DayLocator,MonthLocator

Set the year so we don't have to edit the string labels every year!

In [ ]:
year = 2023

In [ ]:
fig, ax = plt.subplots(figsize=(15,10))
ax.plot (date, maxT, color='red',label = "Max T")
ax.plot (date, minT, color='blue', label = "Min T")
ax.set_title ("ALB Year %d" % year)
ax.set_xlabel('Date')
ax.set_ylabel('Temperature (°F)' )
ax.xaxis.set_major_locator(MonthLocator(interval=1))
dateFmt = DateFormatter('%b %d')
ax.xaxis.set_major_formatter(dateFmt)
ax.legend (loc="best")

## Read in precip data. This will be more challenging due to the presence of T(races).
Let's remind ourselves what the `Dataframe` looks like, paying particular attention to the daily precip column (**PCP**).

In [ ]:
df

<div class="alert alert-warning"> <b>Exercise:</b> define a Pandas <code>DataSeries</code> called <code>precip</code> and populate it with the requisite column from our <code>Dataframe</code>. Then print out its values.</div>

<div class="alert alert-success"> <b>TIP:</b> After you have tried on your own, you can uncomment the first line of the cell below and re-run to <i>load</i> the solution.</div>

In [ ]:
# %load /spare11/atm350/common/feb22/02a.py
precip = df['PCP']

In [ ]:
precip

## The task now is to convert these values from strings to floating point values. Our task is more complicated due to the presence of strings that are clearly not numerical ... such as "T" for *trace*.


### As we did in the first Pandas notebook with max temperatures greater than or equal to 90, create a subset of our `Dataframe` that consists only of those days where precip was a trace.

In [ ]:
traceDays = df[precip=='T']
traceDays

In [ ]:
traceDays.shape

In [ ]:
traceDays.shape[0]

<div class="alert alert-warning"> <b>Exercise:</b> print out the total # of days where a trace of precip was measured. <b><i>Hint</i></b>: look back at how we calculated the total # of 90 degree days in our first Pandas notebook ... we used the <code>shape</code> attribute.</div>

In [ ]:
# %load /spare11/atm350/common/feb22/02b.py
print (df[precip=='T'].shape)
numTraceDays = df[precip == 'T'].shape[0]
print (f"The total # of days in Albany in {year} that had a trace of precipitation was {numTraceDays}")


### Getting back to our task of converting precip amounts from strings to floating point numbers, one thing we could do is to create a new array and populate it via a loop, where we'd use an `if-else` logical test to check for Trace values and set the precip value to 0.00 for each day accordingly.

### There is a more efficient way to do this, though! 
See https://stackoverflow.com/questions/49154068/fixing-a-typeerror-when-using-pandas-after-replacing-a-string-with-a-floating-po?rq=1 

## We use the `loc` method of Pandas to find all elements of a DataSeries with a certain value, and then change that value to something else, all in the same line of code!

### In this case, let's set all values of 'T' to '0.00'

The line below is what we want! Before we execute it, let's break it up into pieces.
``` 
df.loc[df['PCP'] =='T', ['PCP']] = '0.00'
```

#### First, create a `Series` of booleans corresponding to the specified condition.

In [ ]:
df['PCP'] == 'T'

#### Next, build on that cell by using `loc` to display all rows that correspond to the condition being True.

In [ ]:
df.loc[df['PCP'] == 'T']

#### Further build this line of code by only returning the column of interest.

In [ ]:
df.loc[df['PCP'] =='T', ['PCP']]

#### Finally, we have arrived at the full line of code! Take the column of interest, in this case precip only on those days where a trace was measured, and set its value to 0.00.

In [ ]:
df.loc[df['PCP'] =='T', ['PCP']] = '0.00'

In [ ]:
df['PCP']

### This operation actually modifies the `Dataframe` *in place* . We can prove this by printing out a row from a date that we know had a trace amount.

### But first how do we simply print a specific row from a dataframe? Since we know that Jan. 9 had a trace of precip,  try this:

In [ ]:
jan09 = df['DATE'] == '2023-01-09'
jan09

#### That produces a series of booleans; the one matching our condition is `True`. Now we can retrieve all the values for this date.

In [ ]:
df[jan09]

#### We see that the precip has now been set to 0.00.

### Having done this check, and thus re-set the values, let's now convert this series into floating point values.

In [ ]:
precip = df['PCP'].astype("float32")

In [ ]:
precip

### Plot each day's precip total.

In [ ]:
fig, ax = plt.subplots(figsize=(15,10))
ax.plot (date, precip, color='blue', marker='+',label = "Precip")
ax.set_title (f"ALB Year {year}")
ax.set_xlabel('Date')
ax.set_ylabel('Precip (in.)' )
ax.xaxis.set_major_locator(MonthLocator(interval=1))
dateFmt = DateFormatter('%b %d')
ax.xaxis.set_major_formatter(dateFmt)
ax.legend (loc="best")

In [ ]:
# %load /spare11/atm350/common/feb22/02a.py
precipT = df['PCP']

### What if we just want to pick a certain time range? One simple way is to just pass in a subset of our x and y to the `plot` method.

In [ ]:
# Plot out just the trace for October. Corresponds to Julian days 214-245 ... thus, indices 213-244 (why?).
fig, ax = plt.subplots(figsize=(15,10))
ax.plot (date[213:244], precip[213:244], color='blue', marker='+',label = "Precip")
ax.set_title (f"ALB Year {year}")
ax.set_xlabel('Date')
ax.set_ylabel('Precip (in.)' )
ax.xaxis.set_major_locator(MonthLocator(interval=1))
dateFmt = DateFormatter('%b %d')
ax.xaxis.set_major_formatter(dateFmt)
ax.legend (loc="best")

<div class="alert alert-warning"> <b>Exercise:</b> print out a table of days with precip amounts of at least <b>1.00</b> inches. In a separate cell, print out the total # of such days.</div>

In [ ]:
# %load '/spare11/atm350/common/feb22/02c.py'
wetDays = df[precip>=1.00]
wetDays

In [ ]:
# Split the cell here so the table above will be displayed!
numWetDays = wetDays.shape[0]
print (f"The total # of days in Albany in {year} that had at least 1.00 in. of precip was {numWetDays}" )

### Pandas has a function to compute the cumulative sum of a series. We'll use it to compute and graph Albany's total precip over the year.

In [ ]:
precipTotal = precip.cumsum()

In [ ]:
precipTotal

### We can see that the final total is in the last element of the precipTotal array. How can we explicitly print out just this value?

### One of the methods available to us in a Pandas DataSeries is `values`. Let's display it:

In [ ]:
precipTotal.values

<div class="alert alert-warning"> <b>Exercise:</b> It's an array! So, let's print out the last element of the array. What index # can we use?</div>

In [ ]:
# %load '/spare11/atm350/common/feb22/02d.py'
# Print out the value of the last element in the array
precipTotal.values[-1]


### Plot the timeseries of the cumulative precip for Albany over the year.

In [ ]:
fig, ax = plt.subplots(figsize=(15,10))
ax.plot (date, precipTotal, color='blue', marker='.',label = "Precip")
ax.set_title (f"ALB Year {year}")
ax.set_xlabel('Date')
ax.set_ylabel('Precip (in.)' )
ax.xaxis.set_major_locator(MonthLocator(interval=1))
dateFmt = DateFormatter('%b %d')
ax.xaxis.set_major_formatter(dateFmt)
ax.legend (loc="best")

# Pandas has a plethora of statistical analysis methods to apply on tabular data. An excellent summary method is `describe`.

In [ ]:
maxT.describe()

In [ ]:
minT.describe()

In [ ]:
precip.describe()

<div class="alert alert-warning"> <b>Exercise:</b> Why is the <i>mean</i> 0.13, but the <i>median</i> 0.00? Can you write a code cell that answers this question?
    <b>Hint</b>: determine how many days had a trace or less of precip. 
    <ol><li>First, express the condition where precip is equal to 0.00.</li>
        <li>Then, determine the # of rows of that resulting series.</li>
    </ol>
</div>

In [ ]:
# %load /spare11/atm350/common/feb22/02e.py
subset = precip[precip == 0.00]
nRows = subset.shape[0]

print (f"The number of days where precip was a trace or less was {nRows}")
print ("Since this is represents more than half the days of the years, the median must = 0")


### We'll wrap up by calculating and then plotting *rolling means* over a period of days in the year, in order to smooth out the day-to-day variations.

First, let's replot the max and min temperature trace for the entire year, day-by-day.

In [ ]:
fig, ax = plt.subplots(figsize=(15,10))
ax.plot (date, maxT, color='red',label = "Max T")
ax.plot (date, minT, color='blue', label = "Min T")
ax.set_title (f"ALB Year {year}")
ax.set_xlabel('Date')
ax.set_ylabel('Temperature (°F)' )
ax.xaxis.set_major_locator(MonthLocator(interval=1))
dateFmt = DateFormatter('%b %d')
ax.xaxis.set_major_formatter(dateFmt)
ax.legend (loc="best")

Now, let's calculate and plot the daily mean temperature.

In [ ]:
meanT = (maxT + minT) / 2.

In [ ]:
meanT

In [ ]:
fig, ax = plt.subplots(figsize=(15,10))
ax.plot (date, meanT, color='green',label = "Mean T")
ax.set_title (f"ALB Year {year}")
ax.set_xlabel('Date')
ax.set_ylabel('Temperature (°F)' )
ax.xaxis.set_major_locator(MonthLocator(interval=1))
dateFmt = DateFormatter('%b %d')
ax.xaxis.set_major_formatter(dateFmt)
ax.legend (loc="best")

Next, let's use Pandas' `rolling` method to calculate the mean over a specified number of days. We'll center the window at the midpoint of each period (thus, for a 30-day window, the first plotted point will be on Jan. 16 ... covering the Jan. 1 --> Jan. 30 timeframe.

In [ ]:
meanTr5 = meanT.rolling(window=5, center=True)
meanTr10 = meanT.rolling(window=10, center=True)
meanTr15 = meanT.rolling(window=15, center=True)
meanTr30 = meanT.rolling(window=30, center=True)

In [ ]:
meanTr30.mean()

In [ ]:
meanTr5.mean()

In [ ]:
fig, ax = plt.subplots(figsize=(15,10))
ax.plot (date, meanT, color='green',label = "Mean T",alpha=0.2)
ax.plot (date, meanTr5.mean(), color='blue',label = "5 Day", alpha=0.3)
ax.plot (date, meanTr10.mean(), color='purple',label = "10 Day", alpha=0.3)
ax.plot (date, meanTr15.mean(), color='brown',label = "15 Day", alpha=0.3)
ax.plot (date, meanTr30.mean(), color='orange',label = "30 Day", alpha=1.0, linewidth=2)
ax.set_title (f"ALB Year {year}")
ax.set_xlabel('Date')
ax.set_ylabel('Temperature (°F)' )
ax.xaxis.set_major_locator(MonthLocator(interval=1))
dateFmt = DateFormatter('%b %d')
ax.xaxis.set_major_formatter(dateFmt)
ax.legend (loc="best")

Display just the daily and 30-day running mean.

In [ ]:
fig, ax = plt.subplots(figsize=(15,10))
ax.plot (date, meanT, color='green',label = "Mean T",alpha=0.2)
ax.plot (date, meanTr30.mean(), color='orange',label = "30 Day", alpha=1.0, linewidth=2)
ax.set_title (f"ALB Year {year}")
ax.set_xlabel('Date')
ax.set_ylabel('Temperature (°F)' )
ax.xaxis.set_major_locator(MonthLocator(interval=1))
dateFmt = DateFormatter('%b %d')
ax.xaxis.set_major_formatter(dateFmt)
ax.legend (loc="best")